In [2]:
import os
import sys
import math
import datetime
import warnings
import numpy as np
import pandas as pd
import lightgbm as lgb
#import scrapbook as sb
import matplotlib.pyplot as plt

from fclib.common.utils import git_repo_path
from fclib.models.lightgbm import predict
from fclib.evaluation.evaluation_utils import MAPE
from fclib.common.plot import plot_predictions_with_history
from fclib.dataset.ojdata import download_ojdata, split_train_test
from fclib.dataset.ojdata import FIRST_WEEK_START
from fclib.feature_engineering.feature_utils import (
    week_of_month,
    df_from_cartesian_product,
    combine_features,
)

warnings.filterwarnings("ignore")

print("System version: {}".format(sys.version))
print("LightGBM version: {}".format(lgb.__version__))

System version: 3.6.10 |Anaconda, Inc.| (default, May  7 2020, 19:46:08) [MSC v.1916 64 bit (AMD64)]
LightGBM version: 2.3.0


In [4]:
# Data directory
DATA_DIR = os.path.join(git_repo_path(), "smeco data")
DATA_FILE = 'AMI_transposed_with_temps.csv'
#df = pd.read_csv(os.path.join(DATA_DIR, DATA_FILE))
#df

In [59]:
df["DateTime"] = pd.to_datetime(df["DateTime"])
df["month"] = df["DateTime"].dt.month
df["dayofweek"] =  df["DateTime"].dt.dayofweek #The day of the week with Monday=0, Sunday=6.
df["weekofyear"] = df["DateTime"].dt.isocalendar().week
df["hour"] = df["DateTime"].dt.hour
df["is_month_start"] = df["DateTime"].dt.is_month_start
df["is_month_end"] = df["DateTime"].dt.is_month_end
df

DateTime  01676536-A2A5-4BB7-8DA6-6E8993E3E92F  \
0     2019-01-01 01:00:00                                 1.176   
1     2019-01-01 02:00:00                                 1.117   
2     2019-01-01 03:00:00                                 0.825   
3     2019-01-01 04:00:00                                 1.251   
4     2019-01-01 05:00:00                                 1.423   
...                   ...                                   ...   
26298 2021-01-31 19:00:00                                 2.819   
26299 2021-01-31 20:00:00                                 2.866   
26300 2021-01-31 21:00:00                                 2.181   
26301 2021-01-31 22:00:00                                 2.187   
26302 2021-01-31 23:00:00                                 2.158   

       023010C1-B44B-4F84-AAE3-C2A77A738AEF  \
0                                     0.259   
1                                     0.398   
2                                     0.229   
3                                     0.578   
4                                     0.461   
...                                     ...   
26298                                 0.378   
26299                                 0.314   
26300                                 0.594   
26301                                 0.331   
26302                                 0.378   

       025893A0-F07F-4CA4-9FC6-E86A47C132C0  \
0                                     1.692   
1                                     1.456   
2                                     1.475   
3                                     1.327   
4                                     1.497   
...                                     ...   
26298                                 1.203   
26299                                 1.554   
26300                                 1.169   
26301                                 1.180   
26302                                 1.226   

       0295115A-2AD8-404B-8369-F546BC687DF9  \
0                                     1.628   
1                                     0.324   
2                                     0.429   
3                                     0.439   
4                                     0.686   
...                                     ...   
26298                                 0.675   
26299                                 3.444   
26300                                 0.817   
26301                                 1.196   
26302                                 0.701   

       03173585-DA01-46DF-84C4-DB27556CF38A  \
0                                     3.427   
1                                     3.562   
2                                     1.998   
3                                     1.817   
4                                     1.713   
...                                     ...   
26298                                 1.750   
26299                                 1.684   
26300                                 3.102   
26301                                 1.764   
26302                                 1.584   

       032481BE-020A-4899-A8AD-31912A2D8B21  \
0                                     0.648   
1                                     0.453   
2                                     0.702   
3                                     0.831   
4                                     0.592   
...                                     ...   
26298                                 2.174   
26299                                 3.491   
26300                                 2.485   
26301                                 1.708   
26302                                 1.815   

       036039AB-2B04-477B-A696-62D344332399  \
0                                     7.439   
1                                     6.204   
2                                     5.527   
3                                     4.856   
4                                     4.297   
...                                     ...   
26298                                 3.028   
26299      

In [60]:
df["year"]= df["DateTime"].dt.year
df["date"] = df["DateTime"].dt.date
epoch= pd.Timestamp("2019-01-01")  
df["date"] = pd.to_datetime(df["date"]) # due to AttributeError: Can only use .dt accessor with datetimelike values
# Calculation:
df["week"]=np.where(df.date.astype("datetime64").le(epoch), 
                          df.date.dt.week, 
                          df.date.sub(epoch).dt.days//7+52)
df

DateTime  01676536-A2A5-4BB7-8DA6-6E8993E3E92F  \
0     2019-01-01 01:00:00                                 1.176   
1     2019-01-01 02:00:00                                 1.117   
2     2019-01-01 03:00:00                                 0.825   
3     2019-01-01 04:00:00                                 1.251   
4     2019-01-01 05:00:00                                 1.423   
...                   ...                                   ...   
26298 2021-01-31 19:00:00                                 2.819   
26299 2021-01-31 20:00:00                                 2.866   
26300 2021-01-31 21:00:00                                 2.181   
26301 2021-01-31 22:00:00                                 2.187   
26302 2021-01-31 23:00:00                                 2.158   

       023010C1-B44B-4F84-AAE3-C2A77A738AEF  \
0                                     0.259   
1                                     0.398   
2                                     0.229   
3                                     0.578   
4                                     0.461   
...                                     ...   
26298                                 0.378   
26299                                 0.314   
26300                                 0.594   
26301                                 0.331   
26302                                 0.378   

       025893A0-F07F-4CA4-9FC6-E86A47C132C0  \
0                                     1.692   
1                                     1.456   
2                                     1.475   
3                                     1.327   
4                                     1.497   
...                                     ...   
26298                                 1.203   
26299                                 1.554   
26300                                 1.169   
26301                                 1.180   
26302                                 1.226   

       0295115A-2AD8-404B-8369-F546BC687DF9  \
0                                     1.628   
1                                     0.324   
2                                     0.429   
3                                     0.439   
4                                     0.686   
...                                     ...   
26298                                 0.675   
26299                                 3.444   
26300                                 0.817   
26301                                 1.196   
26302                                 0.701   

       03173585-DA01-46DF-84C4-DB27556CF38A  \
0                                     3.427   
1                                     3.562   
2                                     1.998   
3                                     1.817   
4                                     1.713   
...                                     ...   
26298                                 1.750   
26299                                 1.684   
26300                                 3.102   
26301                                 1.764   
26302                                 1.584   

       032481BE-020A-4899-A8AD-31912A2D8B21  \
0                                     0.648   
1                                     0.453   
2                                     0.702   
3                                     0.831   
4                                     0.592   
...                                     ...   
26298                                 2.174   
26299                                 3.491   
26300                                 2.485   
26301                                 1.708   
26302                                 1.815   

       036039AB-2B04-477B-A696-62D344332399  \
0                                     7.439   
1                                     6.204   
2                                     5.527   
3                                     4.856   
4                                     4.297   
...                                     ...   
26298                                 3.028   
26299      

In [61]:
premises = df.columns[1:1501]

In [62]:
non_premise_columns = list(set(df.columns) - set(premises))

In [90]:
# Forecasting settings
'''
n_splits (int, optional): number of splits (folds) to generate (default: 1) 
horizon (int, optional): forecasting horizon, number of weeks to forecast (default: 2) 
gap (int, optional): gap between training and testing, number of weeks between last training 
    week and first test week (default: 2) 
first_week (int, optional): first available week (default: 40) 
last_week (int, optional): last available week (default: 156)

'''


N_SPLITS = 1
HORIZON = 4
GAP = 1
FIRST_WEEK = 1
LAST_WEEK = 160

# Lags, window size, and feature column names
lags = np.arange(2, 20)
window_size = 40
#used_columns = [ "week", "week_of_month", "month", "price", "price_ratio"]

In [83]:
TRAIN_DATA_DIR = os.path.join(DATA_DIR, "train")
TEST_DATA_DIR = os.path.join(DATA_DIR, "test")
if not os.path.isdir(TRAIN_DATA_DIR):
    os.mkdir(TRAIN_DATA_DIR)
if not os.path.isdir(TEST_DATA_DIR):
    os.mkdir(TEST_DATA_DIR)

In [84]:
def _gen_split_indices(n_splits, horizon, gap, first_week, last_week):
    """Generate week splits for given parameters"""
    test_start_index = last_week - (horizon * n_splits) + 1
    train_end_index_first = test_start_index - gap
    train_end_index_last = train_end_index_first + (n_splits - 1) * horizon

    assert (
        test_start_index >= first_week
    ), f"Please adjust your parameters, so that testing data (currently week {test_start_index}), \
         starts after the first available week (week {first_week})."

    assert (
        train_end_index_first >= first_week
    ), f"Please adjust your parameters, so that last training data point (currently week {train_end_index_first}) \
        comes after the first available week (week {first_week})."

    test_start_week_list = list(range(test_start_index, (last_week - horizon + 1) + 1, horizon))
    test_end_week_list = list(range(test_start_index + horizon - 1, last_week + 1, horizon))
    train_end_week_list = list(range(train_end_index_first, train_end_index_last + 1, horizon))
    return test_start_week_list, test_end_week_list, train_end_week_list

In [91]:
test_start_week_list, test_end_week_list, train_end_week_list = _gen_split_indices(
        n_splits= N_SPLITS, 
        horizon=HORIZON, 
        gap=GAP, 
        first_week=FIRST_WEEK, 
        last_week=LAST_WEEK )
print(test_start_week_list, test_end_week_list, train_end_week_list)

[157] [160] [156]


In [80]:
def split_train_test(dataframe, n_splits, horizon, gap, first_week, last_week, data_dir, write_csv):
    """Generate training, testing, and auxiliary datasets. Training data includes the historical 
    sales and external features; testing data contains the future sales and external features; 
    auxiliary data includes the future price, deal, and advertisement information which can be 
    used for making predictions (we assume such auxiliary information is available at the time 
    when we generate the forecasts). Use this function to generate the train, test, aux data for
    each forecast period on the fly, or use write_csv flag to write data to files.
    Note that train_*.csv files in /train folder contain all the features in the training period
    and aux_*.csv files in /train folder contain all the features except 'logmove', 'constant',
    'profit' up until the forecast period end week. Both train_*.csv and auxi_*csv can be used for
    generating forecasts in each split. However, test_*.csv files in /test folder can only be used
    for model performance evaluation.
    Example:
        data_dir = "/home/ojdata"
        train, test, aux = split_train_test(data_dir=data_dir, n_splits=5, horizon=3, write_csv=True)
        print(len(train))
        print(len(test))
        print(len(aux))
    Args:
        data_dir (str): location of the download directory
        n_splits (int, optional): number of splits (folds) to generate (default: 1) 
        horizon (int, optional): forecasting horizon, number of weeks to forecast (default: 2) 
        gap (int, optional): gap between training and testing, number of weeks between last training 
            week and first test week (default: 2) 
        first_week (int, optional): first available week (default: 40) 
        last_week (int, optional): last available week (default: 156)
        write_csv (Boolean, optional): Whether to write out the data files or not (default: False)
    
    Returns:
        list[pandas.DataFrame]: a list containing train data frames for each split
        list[pandas.DataFrame]: a list containing test data frames for each split
        list[pandas.DataFrame]: a list containing aux data frames for each split
        
    """
    # Read data into dataframe
    sales = df

    if write_csv:
        TRAIN_DATA_DIR = os.path.join(data_dir, "train")
        TEST_DATA_DIR = os.path.join(data_dir, "test")
        if not os.path.isdir(TRAIN_DATA_DIR):
            os.mkdir(TRAIN_DATA_DIR)
        if not os.path.isdir(TEST_DATA_DIR):
            os.mkdir(TEST_DATA_DIR)

    train_df_list = list()
    test_df_list = list()
    aux_df_list = list()

    test_start_week_list, test_end_week_list, train_end_week_list = _gen_split_indices(
        n_splits, horizon, gap, first_week, last_week)

    for i in range(n_splits):
        data_mask = (sales.week >= first_week) & (sales.week <= train_end_week_list[i])
        train_df = sales[data_mask].copy()
        data_mask = (sales.week >= test_start_week_list[i]) & (sales.week <= test_end_week_list[i])
        test_df = sales[data_mask].copy()
        data_mask = (sales.week >= first_week) & (sales.week <= test_end_week_list[i])
        aux_df = sales[data_mask].copy()
        #aux_df.drop(["logmove", "constant", "profit"], axis=1, inplace=True)

        if write_csv:
            roundstr = "_" + str(i + 1) if n_splits > 1 else ""
            train_df.to_csv(os.path.join(TRAIN_DATA_DIR, "train" + roundstr + ".csv"))
            test_df.to_csv(os.path.join(TEST_DATA_DIR, "test" + roundstr + ".csv"))
            aux_df.to_csv(os.path.join(TRAIN_DATA_DIR, "auxi" + roundstr + ".csv"))

        train_df_list.append(train_df)
        test_df_list.append(test_df)
        aux_df_list.append(aux_df)

    return train_df_list, test_df_list, aux_df_list

In [92]:
train_df_list, test_df_list, aux_df_list = split_train_test(
    dataframe = df,
    n_splits = N_SPLITS,
    horizon=HORIZON,
    gap=GAP,
    first_week=FIRST_WEEK,
    last_week=LAST_WEEK,
    data_dir = DATA_DIR,
    write_csv=True,)

In [93]:
# Split returns a list, extract the dataframes from the list
train_df = train_df_list[0].reset_index()
test_df = test_df_list[0].reset_index()
aux_df = aux_df_list[0].reset_index()

In [95]:
df.index

RangeIndex(start=0, stop=26303, step=1)

In [96]:
df.index = pd.to_datetime(df.DateTime)
df

DateTime  01676536-A2A5-4BB7-8DA6-6E8993E3E92F  \
DateTime                                                                        
2019-01-01 01:00:00 2019-01-01 01:00:00                                 1.176   
2019-01-01 02:00:00 2019-01-01 02:00:00                                 1.117   
2019-01-01 03:00:00 2019-01-01 03:00:00                                 0.825   
2019-01-01 04:00:00 2019-01-01 04:00:00                                 1.251   
2019-01-01 05:00:00 2019-01-01 05:00:00                                 1.423   
...                                 ...                                   ...   
2021-01-31 19:00:00 2021-01-31 19:00:00                                 2.819   
2021-01-31 20:00:00 2021-01-31 20:00:00                                 2.866   
2021-01-31 21:00:00 2021-01-31 21:00:00                                 2.181   
2021-01-31 22:00:00 2021-01-31 22:00:00                                 2.187   
2021-01-31 23:00:00 2021-01-31 23:00:00                                 2.158   

                     023010C1-B44B-4F84-AAE3-C2A77A738AEF  \
DateTime                                                    
2019-01-01 01:00:00                                 0.259   
2019-01-01 02:00:00                                 0.398   
2019-01-01 03:00:00                                 0.229   
2019-01-01 04:00:00                                 0.578   
2019-01-01 05:00:00                                 0.461   
...                                                   ...   
2021-01-31 19:00:00                                 0.378   
2021-01-31 20:00:00                                 0.314   
2021-01-31 21:00:00                                 0.594   
2021-01-31 22:00:00                                 0.331   
2021-01-31 23:00:00                                 0.378   

                     025893A0-F07F-4CA4-9FC6-E86A47C132C0  \
DateTime                                                    
2019-01-01 01:00:00                                 1.692   
2019-01-01 02:00:00                                 1.456   
2019-01-01 03:00:00                                 1.475   
2019-01-01 04:00:00                                 1.327   
2019-01-01 05:00:00                                 1.497   
...                                                   ...   
2021-01-31 19:00:00                                 1.203   
2021-01-31 20:00:00                                 1.554   
2021-01-31 21:00:00                                 1.169   
2021-01-31 22:00:00                                 1.180   
2021-01-31 23:00:00                                 1.226   

                     0295115A-2AD8-404B-8369-F546BC687DF9  \
DateTime                                                    
2019-01-01 01:00:00                                 1.628   
2019-01-01 02:00:00                                 0.324   
2019-01-01 03:00:00                                 0.429   
2019-01-01 04:00:00                                 0.439   
2019-01-01 05:00:00                                 0.686   
...                                                   ...   
2021-01-31 19:00:00                                 0.675   
2021-01-31 20:00:00                                 3.444   
2021-01-31 21:00:00                                 0.817   
2021-01-31 22:00:00                                 1.196   
2021-01-31 23:00:00                                 0.701   

                     03173585-DA01-46DF-84C4-DB27556CF38A  \
DateTime                                                    
2019-01-01 01:00:00                                 3.427   
2019-01-01 02:00:00                                 3.562   
2019-01-01 03:00:00                                 1.998   
2019-01-01 04:00:00                                 1.817   
2019-01-01 05:00:00                                 1.713   
...                                                   ...   
2021-01-31 19:00:00                                 1.750   
2021-01-31 20:00:00                           

In [150]:
df.DateTime.dt.month.unique()

array([1], dtype=int64)

# new process

In [ ]:
x = pd.read_csv(os.path.join(DATA_DIR, DATA_FILE))


In [252]:
x = pd.read_csv(os.path.join(DATA_DIR, DATA_FILE))
x

DateTime  01676536-A2A5-4BB7-8DA6-6E8993E3E92F  \
0      2019-01-01T01:00:00.0                                 1.176   
1      2019-01-01T02:00:00.0                                 1.117   
2      2019-01-01T03:00:00.0                                 0.825   
3      2019-01-01T04:00:00.0                                 1.251   
4      2019-01-01T05:00:00.0                                 1.423   
...                      ...                                   ...   
26298  2021-01-31T19:00:00.0                                 2.819   
26299  2021-01-31T20:00:00.0                                 2.866   
26300  2021-01-31T21:00:00.0                                 2.181   
26301  2021-01-31T22:00:00.0                                 2.187   
26302  2021-01-31T23:00:00.0                                 2.158   

       023010C1-B44B-4F84-AAE3-C2A77A738AEF  \
0                                     0.259   
1                                     0.398   
2                                     0.229   
3                                     0.578   
4                                     0.461   
...                                     ...   
26298                                 0.378   
26299                                 0.314   
26300                                 0.594   
26301                                 0.331   
26302                                 0.378   

       025893A0-F07F-4CA4-9FC6-E86A47C132C0  \
0                                     1.692   
1                                     1.456   
2                                     1.475   
3                                     1.327   
4                                     1.497   
...                                     ...   
26298                                 1.203   
26299                                 1.554   
26300                                 1.169   
26301                                 1.180   
26302                                 1.226   

       0295115A-2AD8-404B-8369-F546BC687DF9  \
0                                     1.628   
1                                     0.324   
2                                     0.429   
3                                     0.439   
4                                     0.686   
...                                     ...   
26298                                 0.675   
26299                                 3.444   
26300                                 0.817   
26301                                 1.196   
26302                                 0.701   

       03173585-DA01-46DF-84C4-DB27556CF38A  \
0                                     3.427   
1                                     3.562   
2                                     1.998   
3                                     1.817   
4                                     1.713   
...                                     ...   
26298                                 1.750   
26299                                 1.684   
26300                                 3.102   
26301                                 1.764   
26302                                 1.584   

       032481BE-020A-4899-A8AD-31912A2D8B21  \
0                                     0.648   
1                                     0.453   
2                                     0.702   
3                                     0.831   
4                                     0.592   
...                                     ...   
26298                                 2.174   
26299                                 3.491   
26300                                 2.485   
26301                                 1.708   
26302                                 1.815   

       036039AB-2B04-477B-A696-62D344332399  \
0                                     7.439   
1                                     6.204   
2                                     5.527   
3                                     4.856   
4                                     4.297   
...                                     ...   
26298                    

In [253]:
x = x.unstack()
x = x.reset_index()
x

level_0  level_1                      0
0             DateTime        0  2019-01-01T01:00:00.0
1             DateTime        1  2019-01-01T02:00:00.0
2             DateTime        2  2019-01-01T03:00:00.0
3             DateTime        3  2019-01-01T04:00:00.0
4             DateTime        4  2019-01-01T05:00:00.0
...                ...      ...                    ...
39664919  WeatherID_11    26298                  64.44
39664920  WeatherID_11    26299                  72.48
39664921  WeatherID_11    26300                  80.91
39664922  WeatherID_11    26301                  60.39
39664923  WeatherID_11    26302                  51.63

[39664924 rows x 3 columns]

In [254]:
timestamps = x[:26303]

In [255]:
timestamps = timestamps.iloc[:,1:]
timestamps

level_1                      0
0            0  2019-01-01T01:00:00.0
1            1  2019-01-01T02:00:00.0
2            2  2019-01-01T03:00:00.0
3            3  2019-01-01T04:00:00.0
4            4  2019-01-01T05:00:00.0
...        ...                    ...
26298    26298  2021-01-31T19:00:00.0
26299    26299  2021-01-31T20:00:00.0
26300    26300  2021-01-31T21:00:00.0
26301    26301  2021-01-31T22:00:00.0
26302    26302  2021-01-31T23:00:00.0

[26303 rows x 2 columns]

In [256]:
timestamps =  timestamps.rename(columns = {0:'Datetime','level_1':'PK' })
timestamps

PK               Datetime
0          0  2019-01-01T01:00:00.0
1          1  2019-01-01T02:00:00.0
2          2  2019-01-01T03:00:00.0
3          3  2019-01-01T04:00:00.0
4          4  2019-01-01T05:00:00.0
...      ...                    ...
26298  26298  2021-01-31T19:00:00.0
26299  26299  2021-01-31T20:00:00.0
26300  26300  2021-01-31T21:00:00.0
26301  26301  2021-01-31T22:00:00.0
26302  26302  2021-01-31T23:00:00.0

[26303 rows x 2 columns]

In [271]:
x = x[26303:]
x

level_0     PK  value
52606     023010C1-B44B-4F84-AAE3-C2A77A738AEF      0  0.259
52607     023010C1-B44B-4F84-AAE3-C2A77A738AEF      1  0.398
52608     023010C1-B44B-4F84-AAE3-C2A77A738AEF      2  0.229
52609     023010C1-B44B-4F84-AAE3-C2A77A738AEF      3  0.578
52610     023010C1-B44B-4F84-AAE3-C2A77A738AEF      4  0.461
...                                        ...    ...    ...
39664919                          WeatherID_11  26298  64.44
39664920                          WeatherID_11  26299  72.48
39664921                          WeatherID_11  26300  80.91
39664922                          WeatherID_11  26301  60.39
39664923                          WeatherID_11  26302  51.63

[39612318 rows x 3 columns]

In [258]:
x = x.rename(columns = {0:'value','level_1':'PK' })
x

level_0     PK  value
26303     01676536-A2A5-4BB7-8DA6-6E8993E3E92F      0  1.176
26304     01676536-A2A5-4BB7-8DA6-6E8993E3E92F      1  1.117
26305     01676536-A2A5-4BB7-8DA6-6E8993E3E92F      2  0.825
26306     01676536-A2A5-4BB7-8DA6-6E8993E3E92F      3  1.251
26307     01676536-A2A5-4BB7-8DA6-6E8993E3E92F      4  1.423
...                                        ...    ...    ...
39664919                          WeatherID_11  26298  64.44
39664920                          WeatherID_11  26299  72.48
39664921                          WeatherID_11  26300  80.91
39664922                          WeatherID_11  26301  60.39
39664923                          WeatherID_11  26302  51.63

[39638621 rows x 3 columns]

In [259]:
meters = x[26303: 26303* 1500] #1500 is number of meters
meters

level_0     PK  value
52606     023010C1-B44B-4F84-AAE3-C2A77A738AEF      0  0.259
52607     023010C1-B44B-4F84-AAE3-C2A77A738AEF      1  0.398
52608     023010C1-B44B-4F84-AAE3-C2A77A738AEF      2  0.229
52609     023010C1-B44B-4F84-AAE3-C2A77A738AEF      3  0.578
52610     023010C1-B44B-4F84-AAE3-C2A77A738AEF      4  0.461
...                                        ...    ...    ...
39480798  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26298  4.815
39480799  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26299   1.48
39480800  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26300  0.878
39480801  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26301  1.915
39480802  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26302   1.24

[39428197 rows x 3 columns]

In [260]:
meters =  meters.rename(columns = {'level_0':'meterID','value':'kwh' })
meters

meterID     PK    kwh
52606     023010C1-B44B-4F84-AAE3-C2A77A738AEF      0  0.259
52607     023010C1-B44B-4F84-AAE3-C2A77A738AEF      1  0.398
52608     023010C1-B44B-4F84-AAE3-C2A77A738AEF      2  0.229
52609     023010C1-B44B-4F84-AAE3-C2A77A738AEF      3  0.578
52610     023010C1-B44B-4F84-AAE3-C2A77A738AEF      4  0.461
...                                        ...    ...    ...
39480798  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26298  4.815
39480799  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26299   1.48
39480800  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26300  0.878
39480801  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26301  1.915
39480802  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B  26302   1.24

[39428197 rows x 3 columns]

In [262]:
weather = x[26303* 1500:] #1500 is number of meters
weather

level_0     PK  value
39480803   WeatherID_5      0  17.13
39480804   WeatherID_5      1  36.48
39480805   WeatherID_5      2  42.05
39480806   WeatherID_5      3  65.29
39480807   WeatherID_5      4  74.63
...                ...    ...    ...
39664919  WeatherID_11  26298  64.44
39664920  WeatherID_11  26299  72.48
39664921  WeatherID_11  26300  80.91
39664922  WeatherID_11  26301  60.39
39664923  WeatherID_11  26302  51.63

[184121 rows x 3 columns]

In [263]:
weather =  weather.rename(columns = {'value':'temp', 'level_0':'StationID'})
weather

StationID     PK   temp
39480803   WeatherID_5      0  17.13
39480804   WeatherID_5      1  36.48
39480805   WeatherID_5      2  42.05
39480806   WeatherID_5      3  65.29
39480807   WeatherID_5      4  74.63
...                ...    ...    ...
39664919  WeatherID_11  26298  64.44
39664920  WeatherID_11  26299  72.48
39664921  WeatherID_11  26300  80.91
39664922  WeatherID_11  26301  60.39
39664923  WeatherID_11  26302  51.63

[184121 rows x 3 columns]

In [267]:
timestamps.Datetime = pd.date_range("2019-01-01", periods=26303, freq="H")

In [268]:
timestamps

PK            Datetime
0          0 2019-01-01 00:00:00
1          1 2019-01-01 01:00:00
2          2 2019-01-01 02:00:00
3          3 2019-01-01 03:00:00
4          4 2019-01-01 04:00:00
...      ...                 ...
26298  26298 2021-12-31 18:00:00
26299  26299 2021-12-31 19:00:00
26300  26300 2021-12-31 20:00:00
26301  26301 2021-12-31 21:00:00
26302  26302 2021-12-31 22:00:00

[26303 rows x 2 columns]

In [269]:
timestamps.merge(meters,on = 'PK').merge(weather, on = 'PK')

MemoryError: Unable to allocate 301. MiB for an array with shape (1, 39428197) and data type object

In [270]:
df = timestamps.merge(meters,on = 'PK')

MemoryError: Unable to allocate 301. MiB for an array with shape (1, 39428197) and data type object

In [5]:
x = pd.read_csv(os.path.join(DATA_DIR, DATA_FILE))
x = x.unstack()
x = x.reset_index()
timestamps = x[:26303]
timestamps = timestamps.iloc[:,1:]
timestamps =  timestamps.rename(columns = {0:'Datetime','level_1':'PK' })
x = x[26303:]
x = x.rename(columns = {0:'value','level_1':'PK' })
meters = x[26303: 26303* 1500] #1500 is number of meters
meters =  meters.rename(columns = {'level_0':'meterID','value':'kwh' })
timestamps.Datetime = pd.date_range("2019-01-01", periods=26303, freq="H")
df = timestamps.merge(meters,on = 'PK')

In [6]:
df

PK            Datetime                               meterID  \
0             0 2019-01-01 00:00:00  023010C1-B44B-4F84-AAE3-C2A77A738AEF   
1             0 2019-01-01 00:00:00  025893A0-F07F-4CA4-9FC6-E86A47C132C0   
2             0 2019-01-01 00:00:00  0295115A-2AD8-404B-8369-F546BC687DF9   
3             0 2019-01-01 00:00:00  03173585-DA01-46DF-84C4-DB27556CF38A   
4             0 2019-01-01 00:00:00  032481BE-020A-4899-A8AD-31912A2D8B21   
...         ...                 ...                                   ...   
39428192  26302 2021-12-31 22:00:00  FF9A11FE-372C-43F9-A565-70DDA7C5BF28   
39428193  26302 2021-12-31 22:00:00  FFBECBBF-C646-43F0-A3BB-1C3DC7946CF9   
39428194  26302 2021-12-31 22:00:00  FFC850B6-B967-42C4-A11F-F3F2CD8DF75B   
39428195  26302 2021-12-31 22:00:00  FFCBFBD9-0C90-4FBD-83EE-09E6AD6AC240   
39428196  26302 2021-12-31 22:00:00  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B   

            kwh  
0         0.259  
1         1.692  
2         1.628  
3         3.427  
4         0.648  
...         ...  
39428192  0.958  
39428193  0.339  
39428194  0.997  
39428195  2.598  
39428196   1.24  

[39428197 rows x 4 columns]

In [7]:
df["Datetime"] = pd.to_datetime(df["Datetime"])
df["month"] = df["Datetime"].dt.month
df["dayofweek"] =  df["Datetime"].dt.dayofweek #The day of the week with Monday=0, Sunday=6.
df["weekofyear"] = df["Datetime"].dt.isocalendar().week
df["hour"] = df["Datetime"].dt.hour
df["is_month_start"] = df["Datetime"].dt.is_month_start
df["is_month_end"] = df["Datetime"].dt.is_month_end
df["year"]= df["Datetime"].dt.year
df["date"] = df["Datetime"].dt.date
epoch= pd.Timestamp("2019-01-01")  
df["date"] = pd.to_datetime(df["date"]) # due to AttributeError: Can only use .dt accessor with datetimelike values
# Calculation:
df["week"]=np.where(df.date.astype("datetime64").le(epoch), 
                          df.date.dt.week, 
                          df.date.sub(epoch).dt.days//7+52)
df

PK            Datetime                               meterID  \
0             0 2019-01-01 00:00:00  023010C1-B44B-4F84-AAE3-C2A77A738AEF   
1             0 2019-01-01 00:00:00  025893A0-F07F-4CA4-9FC6-E86A47C132C0   
2             0 2019-01-01 00:00:00  0295115A-2AD8-404B-8369-F546BC687DF9   
3             0 2019-01-01 00:00:00  03173585-DA01-46DF-84C4-DB27556CF38A   
4             0 2019-01-01 00:00:00  032481BE-020A-4899-A8AD-31912A2D8B21   
...         ...                 ...                                   ...   
39428192  26302 2021-12-31 22:00:00  FF9A11FE-372C-43F9-A565-70DDA7C5BF28   
39428193  26302 2021-12-31 22:00:00  FFBECBBF-C646-43F0-A3BB-1C3DC7946CF9   
39428194  26302 2021-12-31 22:00:00  FFC850B6-B967-42C4-A11F-F3F2CD8DF75B   
39428195  26302 2021-12-31 22:00:00  FFCBFBD9-0C90-4FBD-83EE-09E6AD6AC240   
39428196  26302 2021-12-31 22:00:00  FFED5B43-ACCA-4A5F-9E34-D5AF3EE5956B   

            kwh  month  dayofweek  weekofyear  hour  is_month_start  \
0         0.259      1          1           1     0            True   
1         1.692      1          1           1     0            True   
2         1.628      1          1           1     0            True   
3         3.427      1          1           1     0            True   
4         0.648      1          1           1     0            True   
...         ...    ...        ...         ...   ...             ...   
39428192  0.958     12          4          52    22           False   
39428193  0.339     12          4          52    22           False   
39428194  0.997     12          4          52    22           False   
39428195  2.598     12          4          52    22           False   
39428196   1.24     12          4          52    22           False   

          is_month_end  year       date  week  
0                False  2019 2019-01-01     1  
1                False  2019 2019-01-01     1  
2                False  2019 2019-01-01     1  
3                False  2019 2019-01-01     1  
4                False  2019 2019-01-01     1  
...                ...   ...        ...   ...  
39428192          True  2021 2021-12-31   208  
39428193          True  2021 2021-12-31   208  
39428194          True  2021 2021-12-31   208  
39428195          True  2021 2021-12-31   208  
39428196          True  2021 2021-12-31   208  

[39428197 rows x 13 columns]

In [8]:
l = df['meterID'].tolist()

In [9]:
len(l)

39428197

In [10]:
d = dict([(y,x+1) for x,y in enumerate(sorted(set(l)))])

In [11]:
len(d)

1499

In [12]:
coded= [d[x] for x in l]
len(coded)

39428197

In [13]:
df['meterID'] = coded
df

PK            Datetime  meterID    kwh  month  dayofweek  \
0             0 2019-01-01 00:00:00        1  0.259      1          1   
1             0 2019-01-01 00:00:00        2  1.692      1          1   
2             0 2019-01-01 00:00:00        3  1.628      1          1   
3             0 2019-01-01 00:00:00        4  3.427      1          1   
4             0 2019-01-01 00:00:00        5  0.648      1          1   
...         ...                 ...      ...    ...    ...        ...   
39428192  26302 2021-12-31 22:00:00     1495  0.958     12          4   
39428193  26302 2021-12-31 22:00:00     1496  0.339     12          4   
39428194  26302 2021-12-31 22:00:00     1497  0.997     12          4   
39428195  26302 2021-12-31 22:00:00     1498  2.598     12          4   
39428196  26302 2021-12-31 22:00:00     1499   1.24     12          4   

          weekofyear  hour  is_month_start  is_month_end  year       date  \
0                  1     0            True         False  2019 2019-01-01   
1                  1     0            True         False  2019 2019-01-01   
2                  1     0            True         False  2019 2019-01-01   
3                  1     0            True         False  2019 2019-01-01   
4                  1     0            True         False  2019 2019-01-01   
...              ...   ...             ...           ...   ...        ...   
39428192          52    22           False          True  2021 2021-12-31   
39428193          52    22           False          True  2021 2021-12-31   
39428194          52    22           False          True  2021 2021-12-31   
39428195          52    22           False          True  2021 2021-12-31   
39428196          52    22           False          True  2021 2021-12-31   

          week  
0            1  
1            1  
2            1  
3            1  
4            1  
...        ...  
39428192   208  
39428193   208  
39428194   208  
39428195   208  
39428196   208  

[39428197 rows x 13 columns]

In [14]:
df.dtypes

PK                         int64
Datetime          datetime64[ns]
meterID                    int64
kwh                       object
month                      int64
dayofweek                  int64
weekofyear                UInt32
hour                       int64
is_month_start              bool
is_month_end                bool
year                       int64
date              datetime64[ns]
week                       int64
dtype: object

In [15]:
df['kwh'] = pd.to_numeric(df['kwh'])
df.dtypes

PK                         int64
Datetime          datetime64[ns]
meterID                    int64
kwh                      float64
month                      int64
dayofweek                  int64
weekofyear                UInt32
hour                       int64
is_month_start              bool
is_month_end                bool
year                       int64
date              datetime64[ns]
week                       int64
dtype: object

In [16]:
df.columns

Index(['PK', 'Datetime', 'meterID', 'kwh', 'month', 'dayofweek', 'weekofyear',
       'hour', 'is_month_start', 'is_month_end', 'year', 'date', 'week'],
      dtype='object')

In [17]:
train = df[df.year<2021]
test = df[df.year ==2021]

In [18]:
train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26298456 entries, 0 to 26298455
Data columns (total 13 columns):
 #   Column          Dtype         
---  ------          -----         
 0   PK              int64         
 1   Datetime        datetime64[ns]
 2   meterID         int64         
 3   kwh             float64       
 4   month           int64         
 5   dayofweek       int64         
 6   weekofyear      UInt32        
 7   hour            int64         
 8   is_month_start  bool          
 9   is_month_end    bool          
 10  year            int64         
 11  date            datetime64[ns]
 12  week            int64         
dtypes: UInt32(1), bool(2), datetime64[ns](2), float64(1), int64(7)
memory usage: 2.3 GB


In [19]:
test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 13129741 entries, 26298456 to 39428196
Data columns (total 13 columns):
 #   Column          Dtype         
---  ------          -----         
 0   PK              int64         
 1   Datetime        datetime64[ns]
 2   meterID         int64         
 3   kwh             float64       
 4   month           int64         
 5   dayofweek       int64         
 6   weekofyear      UInt32        
 7   hour            int64         
 8   is_month_start  bool          
 9   is_month_end    bool          
 10  year            int64         
 11  date            datetime64[ns]
 12  week            int64         
dtypes: UInt32(1), bool(2), datetime64[ns](2), float64(1), int64(7)
memory usage: 1.2 GB


In [20]:
X = train[['meterID', 'month', 'dayofweek', 'weekofyear',
       'hour', 'is_month_start', 'is_month_end', 'year', 'week']]
X = X.values
Y= train[['kwh']]
Y= Y.values

In [21]:
import sklearn
sklearn.__version__

'0.24.2'

In [22]:
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Lasso
from sklearn.linear_model import ElasticNet
from sklearn.tree import DecisionTreeRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.metrics import mean_squared_error

In [23]:
validation_size = 0.20
seed = 7
X_train, X_validation, Y_train, Y_validation = train_test_split(X, Y,
test_size=validation_size, random_state=seed)

In [26]:
# Test options and evaluation metric
num_folds = 10
seed = 7
scoring = 'neg_mean_squared_error'

# Spot-Check Algorithms
models = []

models.append(('CART', DecisionTreeRegressor()))
models.append(('RF',RandomForestRegressor()))


# evaluate each model in turn
results = []
names = []
for name, model in models:
    kfold = KFold(n_splits=num_folds)
    cv_results = cross_val_score(model, X_train, Y_train, cv=kfold, scoring=scoring)
    results.append(cv_results)
    names.append(name)
    msg = "%s: %f (%f)" % (name, cv_results.mean(), cv_results.std())
    print(msg)

CART: nan (nan)
RF: nan (nan)


In [27]:
t = df[[ 'Datetime', 'meterID', 'kwh']]

In [ ]:
from joblib import Parallel, delayed
import multiprocessing
# what are your inputs, and what operation do you want to
# perform on each input. For example...
inputs = range(10)
def processInput(i):
    return i * i
num_cores = multiprocessing.cpu_count()
results = Parallel(n_jobs=num_cores)(delayed(processInput)(i) for i in inputs

In [32]:
#lagged feature creation
#so slow
from joblib import Parallel, delayed
import multiprocessing
from tqdm import tqdm
kwh_lag_1 = []
def lagged_value(i):
    time_stamp = t.iloc[i]['Datetime']
    time_stamp_lag_1 = time_stamp- datetime.timedelta(hours = 1)
    meter_id = t.iloc[i]['meterID']
    temp = t[(t.Datetime == time_stamp_lag_1) & (t.meterID == meter_id)]
    if temp.empty:
        kwh_lag_1.append(np.nan)
    else:
        kwh_lag_1.append(temp.kwh)

kwh_lag_1 = []
num_cores = multiprocessing.cpu_count()
Parallel(n_jobs=num_cores)(delayed(lagged_value)(i) for i in tqdm(range(t.shape[0])))

'''
for i in tqdm(range(39428197)):
     kwh_lag_1.append(lagged_value(i))
'''


  0%|                                                                     | 3072/39428197 [06:13<1194:53:57,  9.17it/s]

KeyboardInterrupt: 

In [33]:
num_cores = multiprocessing.cpu_count()

In [34]:
num_cores

12

In [35]:
import asyncio
import time
def background(f):
    def wrapped(*args, **kwargs):
        return asyncio.get_event_loop().run_in_executor(None, f, *args, **kwargs)

    return wrapped

@background
def lagged_value(i):
    time_stamp = t.iloc[i]['Datetime']
    time_stamp_lag_1 = time_stamp- datetime.timedelta(hours = 1)
    meter_id = t.iloc[i]['meterID']
    temp = t[(t.Datetime == time_stamp_lag_1) & (t.meterID == meter_id)]
    if temp.empty:
        kwh_lag_1.append(np.nan)
    else:
        kwh_lag_1.append(temp.kwh)
        
kwh_lag_1 = []
for i in tqdm(range(t.shape[0])):
    lagged_value(i)


print('loop finished')


  0%|                                                                     | 35108/39428197 [02:06<27:40:08, 395.48it/s]


  0%|                                                                     | 58498/39428197 [04:46<16:21:14, 668.71it/s]


  0%|▏                                                                    | 88919/39428197 [07:12<36:40:39, 297.94it/s]


  0%|▏                                                                   | 118423/39428197 [09:37<134:45:29, 81.03it/s]


  0%|▎                                                                   | 164166/39428197 [12:20<21:49:38, 499.68it/s]


...

 38%|███████████████████████▉                                       | 14956997/39428197 [17:23:20<17:56:31, 378.86it/s]


 38%|███████████████████████▉                                       | 14995974/39428197 [17:25:59<42:33:51, 159.45it/s]


 38%|████████████████████████▍                                       | 15031929/39428197 [17:28:50<80:46:37, 83.89it/s]


 38%|████████████████████████                                       | 15045986/39428197 [17:29:44<28:21:07, 238.88it/s]


KeyboardInterrupt: 

In [1]:
!pip install autots

  Using cached statsmodels-0.12.2-cp36-none-win_amd64.whl (9.3 MB)
  Using cached patsy-0.5.2-py2.py3-none-any.whl (233 kB)


In [2]:
from autots import AutoTS

In [5]:
from autots import load_hourly
df = load_hourly()
df

datetime     series_id         value
0      2016-10-01 00:00:00    clouds_all            20
1      2016-10-01 01:00:00    clouds_all            20
2      2016-10-01 02:00:00    clouds_all            56
3      2016-10-01 03:00:00    clouds_all            56
4      2016-10-01 04:00:00    clouds_all            56
...                    ...           ...           ...
105115 2018-09-30 19:00:00  weather_main        Clouds
105116 2018-09-30 20:00:00  weather_main        Clouds
105117 2018-09-30 21:00:00  weather_main  Thunderstorm
105118 2018-09-30 22:00:00  weather_main        Clouds
105119 2018-09-30 23:00:00  weather_main        Clouds

[105120 rows x 3 columns]

In [9]:
long = True
df = load_hourly(long = long)
df

clouds_all  rain_1h  snow_1h    temp  traffic_volume  \
datetime                                                                    
2016-10-01 00:00:00        20.0      0.0      0.0  286.22          1195.0   
2016-10-01 01:00:00        20.0      0.0      0.0  285.60           776.0   
2016-10-01 02:00:00        56.0      0.0      0.0  285.49           666.0   
2016-10-01 03:00:00        56.0      0.0      0.0  284.59           448.0   
2016-10-01 04:00:00        56.0      0.0      0.0  284.26           512.0   
...                         ...      ...      ...     ...             ...   
2018-09-30 19:00:00        75.0      0.0      0.0  283.45          3543.0   
2018-09-30 20:00:00        90.0      0.0      0.0  282.76          2781.0   
2018-09-30 21:00:00        90.0      0.0      0.0  282.73          2159.0   
2018-09-30 22:00:00        90.0      0.0      0.0  282.09          1450.0   
2018-09-30 23:00:00        90.0      0.0      0.0  282.12           954.0   

                     weather_main  
datetime                           
2016-10-01 00:00:00        Clouds  
2016-10-01 01:00:00        Clouds  
2016-10-01 02:00:00        Clouds  
2016-10-01 03:00:00        Clouds  
2016-10-01 04:00:00        Clouds  
...                           ...  
2018-09-30 19:00:00        Clouds  
2018-09-30 20:00:00        Clouds  
2018-09-30 21:00:00  Thunderstorm  
2018-09-30 22:00:00        Clouds  
2018-09-30 23:00:00        Clouds  

[17520 rows x 6 columns]

In [6]:
df.series_id.unique()

array(['clouds_all', 'rain_1h', 'snow_1h', 'temp', 'traffic_volume',
       'weather_main'], dtype=object)

In [7]:
model = AutoTS(
    forecast_length=21,
    frequency='infer',
    prediction_interval=0.9,
    ensemble=None,
    model_list="fast",  # "superfast", "default", "fast_parallel"
    transformer_list="fast",  # "superfast",
    drop_most_recent=1,
    max_generations=4,
    num_validations=2,
    validation_method="backwards"
)
model = model.fit(
    df,
    date_col='datetime' if long else None,
    value_col='value' if long else None,
    id_col='series_id' if long else None,
)

prediction = model.predict()
# plot a sample
prediction.plot(model.df_wide_numeric,
                series=model.df_wide_numeric.columns[0],
                start_date="2019-01-01")
# Print the details of the best model
print(model)

# point forecasts dataframe
forecasts_df = prediction.forecast
# upper and lower forecasts
forecasts_up, forecasts_low = prediction.upper_forecast, prediction.lower_forecast

# accuracy of all tried model results
model_results = model.results()
# and aggregated from cross validation
validation_results = model.results("validation")

NameError: name 'long' is not defined